# Reflection `IEnumerable`
This notebook explores the ways to access an `IEnumerable` through reflection.

In [ ]:
public class TestItem
{
    public string Name { get; set; } = string.Empty;
}

public class Test
{
    public string Name { get; set; } = string.Empty;
    public List<TestItem> Items { get; set; } = new();
}

In [ ]:
var testInstance = new Test();
testInstance.Name = "Camera";

testInstance.Items.Add(new() { Name = "Microphone jack" });
testInstance.Items.Add(new() { Name = "Hotshoe" });
testInstance.Items.Add(new() { Name = "Bayonet" });

In [ ]:
using System.Diagnostics;
using System.Reflection;

public string[] GetNameValues(object obj, string propertyName)
{
    List<string> retVal = new();
    var objProperties = obj.GetType().GetProperties();

    foreach (var prop in objProperties)
    {
        var propVal = prop.GetValue(obj);
        if (propVal == null) {
            Debug.WriteLine($"Skipping property \"{prop.Name}\" with null value");
        }

        if (prop.Name == "Name") {
            Debug.WriteLine($"Found property named \"{propertyName}\"");
            retVal.Add(propVal.ToString());
        } else if (typeof(string) != prop.PropertyType && typeof(IEnumerable).IsAssignableFrom(prop.PropertyType)) {
            Debug.WriteLine($"Property \"{prop.Name}\" is enumerable");
            
            foreach (var item in (IEnumerable)propVal)
            {
                retVal.AddRange(GetNameValues(item, propertyName));
            }
        }
    }

    return retVal.ToArray();
}

display(GetNameValues(testInstance, "Name"));

index value 0 Camera 1 Microphone jack 2 Hotshoe 3 Bayonet